## **Optimization Route and Plotting on Map using Open Route Service and OR-TOOLS**
Notebook ini digunakan untuk memperoleh rute optimal yang didasarkan pada rute jarak sebenarnya di lapangan. Dengan menggunakan dua *tools open source*, yaitu Open Route Service (ORS) untuk memperoleh matriks jarak dan rute perjalanan berdasarkan profil kendaraan dan OR-TOOLS untuk memperoleh titik urutan kunjungan berdasarkan jarak, demand, kapasitas kendaraan, dan jumlah kendaraan.

#### **`Open Route Service`**
`OpenRouteService (ORS)` adalah platform open-source yang menyediakan layanan untuk perencanaan rute dan analisis geografis berbasis data geospasial. ORS memanfaatkan data dari OpenStreetMap (OSM), yang merupakan peta jalan global sumber terbuka. Layanan ini memungkinkan pengguna untuk membuat aplikasi berbasis peta dan melakukan berbagai analisis rute.

Berikut poin-poin penting tentang **OpenRouteService (ORS)**:

1. **Fungsi Utama**  
   - **Routing:** Menyediakan rute optimal untuk mobil, sepeda, jalan kaki, dll.  
   - **Isochrones:** Membuat area jangkauan berdasarkan waktu/jarak.  
   - **Optimasi Rute:** Rute optimal untuk banyak titik (misalnya, pengiriman barang).  
   - **Analisis Aksesibilitas:** Menilai jangkauan lokasi tertentu.  

2. **Berbasis OpenStreetMap:**  
   Memanfaatkan data sumber terbuka yang akurat dan dapat diperbarui.

3. **API Layanan:**  
   Tersedia berbagai API seperti routing, geocoding, isochrones, dan pelacakan jarak.

4. **Open-Source:**  
   Gratis untuk diakses dengan fitur yang dapat dikembangkan sesuai kebutuhan.  

5. **Aplikasi Utama:**  
   Cocok untuk transportasi, logistik, analisis geografis, dan aplikasi berbasis peta.

Sumber: https://openrouteservice.org/

#### **`OR-TOOLS`**
OR-Tools adalah pustaka optimasi open-source yang dikembangkan oleh Google untuk menyelesaikan masalah optimasi kombinatorial. Pustaka ini dirancang untuk menangani berbagai skenario seperti rute kendaraan, penjadwalan tugas, alokasi sumber daya, dan masalah optimasi lainnya. OR-Tools sangat fleksibel dan mendukung berbagai metode pemrograman seperti Linear Programming (LP), Mixed-Integer Programming (MIP), dan Constraint Programming (CP).

1. **Fungsi Utama**  
   - **Optimasi Rute:** Menyelesaikan masalah rute kendaraan (Vehicle Routing Problem, VRP) dengan kendala waktu, kapasitas, dan prioritas.  
   - **Penjadwalan:** Mengatur urutan tugas dengan efisiensi tinggi.  
   - **Optimasi Kombinatorial:** Memecahkan masalah seperti alokasi sumber daya atau pencocokan.

2. **Dikembangkan oleh Google**  
   Platform ini dipercaya di industri karena keandalan dan fleksibilitasnya.

3. **Solver yang Didukung**  
   - Linear Programming (LP)  
   - Mixed-Integer Programming (MIP)  
   - Constraint Programming (CP)  
   - Dan lain-lain.

4. **Kompatibilitas Bahasa Pemrograman**  
   Mendukung integrasi dengan Python, C++, Java, dan C#, memudahkan pengguna dengan berbagai kebutuhan teknis.

5. **Aplikasi Utama**  
   - Logistik dan transportasi  
   - Penjadwalan produksi  
   - Manajemen rantai pasok  
   - Perencanaan bisnis lainnya.  

OR-Tools digunakan secara luas karena fleksibilitasnya dalam menangani masalah dengan banyak kendala, baik untuk penelitian maupun aplikasi dunia nyata.

Sumber: https://developers.google.com/optimization/introduction

#### **`Perolehan Data`**
Data diperoleh dari dua sumber. Pertama, melalui **`(Versi 57 DC) Data Optimasi Distribusi Jawa Tengah`** pada tab sheet "Sheet2" yang berisi 8264 data desa beserta alokasi yang diperoleh dari perhitungan **`alokasi_jawa_tengah.xlsx`** yang di-*merge* dalam **`preprocessing_data.ipynb`**. Setelahnya, akan dibentuk clustering menggunakan pendekatan K-Means, menghitung jumlah cluster optimal menggunakan elbow method dan silhouette score, setelahnya memasukkan jumlah clustering itu dengan menggunakan koordinat latitude dan longitude serta demand sebagai variabel yang dipertimbangkan untuk membagi data pelanggan. Semua itu bisa dilakukan di dalam file **`generate_cluster.ipynb`**.

In [3]:
import folium
import folium.plugins
from folium.plugins import MarkerCluster
import folium.plugins.antpath
from openrouteservice import client, places, distance_matrix
from shapely import wkt, geometry
from ortools.constraint_solver import pywrapcp, routing_enums_pb2
import pandas as pd
import requests
import math
import json

## **Variable**
Jumlah kendaraan harus lebih besar daripada jumlah permintaan. Kode dibawah sudah otomatis dapat menyeleksi berapa kendaraan yang dibutuhkan untuk mengantarkan seluruh demand, sehingga menempatkan jumlah nilai kendaraan sangat tinggi tidak masalah, tetapi harus dipertimbangkan bahwa itu dapat mengurangi kemampuan mencari solusi optimal atau bahkan bisa membuat error, sehingga jangan diatur juga terlalu tinggi.

In [4]:
# the input variable
num_vehicle = 2000
vehicle_capacity = 8 # satuannya bisa apapun
data_raw = "desa_45.xlsx"
sheet_name = "dc_24"

map_name = "map_desa_24.html"

## **Mengambil Data mentah**

Mengambil data dalam bentuk **EXCEL** dengan kolom penting seperti
|  **Key** |  **Tipe** |  **Deskripsi**|
|---|---|---|
| Name* | *string* | Nama Desa atau DC
| Latitude* | *float* | Koordinat Latitude
| Longitude* | *float* | Koordinat Longitude
| Demand* | *float* | Jumlah Permintaan/alokasi
| Address | *string* | Alamat Titik
| Provinsi | *string* | Identifikasi Provinsi
| Distance | *float* | Jarak Data
| *) kolom yang wajib ada| | 

**PENTING: baris pertama dalam data WAJIB adalah DC yang demand dan distance di atur ke angka 0**

contoh: menggunakan data DC ke-24 pada excel "desa_45.xlsx"

In [5]:
dataset = pd.read_excel(data_raw,sheet_name=sheet_name)
dataset

Name Address     Provinsi  Latitude   Longitude  Demand  Distance
0           DC24       -  JAWA TENGAH -6.936271  111.166665    0.00   0.00000
1    PUNCAKWANGI       -  JAWA TENGAH -6.840550  111.175000   16.66  14.47279
2       KETILENG       -  JAWA TENGAH -6.956400  111.175000   44.23   3.98228
3          LEDOK       -  JAWA TENGAH -6.885710  111.222000   44.23  10.97205
4    SUMBERAGUNG       -  JAWA TENGAH -6.998650  111.149000   53.45  10.57289
..           ...     ...          ...       ...         ...     ...       ...
58     MOJOAGUNG       -  JAWA TENGAH -6.864610  111.175000   16.66  11.73984
59  KEMADAHBATUR       -  JAWA TENGAH -6.996220  111.033000   53.45  25.31675
60    KARANGAWEN       -  JAWA TENGAH -6.909910  111.037000   16.66  32.56616
61    KARANGASEM       -  JAWA TENGAH -7.008700  111.117000   53.45  18.78137
62      GAPLOKAN       -  JAWA TENGAH -6.892070  111.277000   44.23  23.31479

[63 rows x 7 columns]

## **Open Route Service "Matrix" Endpoint**

#### Endpoint - /v2/matrix/{profile}
Blok ini berusaha untuk mengambil distance matrix berdasarkan koordinat data dari titik desa menggunakan API Endpoint **Matrix** pada **Open Route Service**. Hasil berupa matriks jarak dalam satuan **meter** yang telah mempertimbangkan **jarak sebenarnya** di peta yang diambil berdasarkan rekomendasi jarak dan waktu yang disediakan oleh Open Route Service. Ada beberapa key request yang bisa dimanfaatkan, parameter ini akan dimasukkan dalam body request sebagai permintaan untuk API Open Route Service

| **Key**              | **Type**      | **Def. Value**  | **Deskripsi**                                                                                   |
|-----------------------|---------------|------------------|-------------------------------------------------------------------------------------------------|
| locations*           | array list    | -                | List data dari titik-titik konsumen, termasuk koordinat **depot pada baris pertama**. Jika distance matrix = 0, maka matriks jarak menghitung titik itu sendiri atau menghindari error. struktur data adalah **`(lon, lat)`** |
| profile*             | string        | -                | Menentukan tipe kendaraan (saat ini hanya menyediakan tipe data **driving-hgv**).               |
| destinations         | array list    | all data              | Indeks yang menjadi destination point dalam perhitungan matriks jarak. Default adalah semua data |
| sources              | array list    | all data                | Indeks yang menjadi source. Jika kosong, maka defaultnya adalah semua data|
| id                   | string        | -                | Menambahkan key "id" pada output di "key metadata".                                            |
| metrics              | array         | duration         | Mengembalikan nilai distance matrix dalam bentuk durasi (waktu) atau jarak (distance).         |
| units                | string        | m                | Menentukan satuan jarak ("km", "m", atau "mi").                                                |
| profileName          | string        | -                | Penamaan profil di body JSON.                                                                  |
| resolve_locations    | boolean       | false            | Menentukan apakah lokasi sudah ditentukan atau belum. Jika "true", setiap elemen di "destinations" dan "sources" akan berisi elemen "name" yang mengidentifikasi nama jalan terdekat. |

Output berupa respon json yang berisi distance/duration, destinations, sources, dan metadata.
*) -> kolom yang wajib ada

Hasil data berbentuk JSON file yang dapat dibaca menggunakan **modul JSON** Python, baik dalam *success* maupun *error response*.
Seluruh dokumentasi lengkap mengenai fitur Open Route Service dapat dibaca dalam link berikut **https://giscience.github.io/openrouteservice/** 

Domain URL menggunakan ***ds-route-service-api.pupuk.in*** yang telah dibuat server lokalnya

In [6]:
village_coords = [(coords["Longitude"], coords["Latitude"]) for _,coords in dataset.iterrows()]

request = {'locations': village_coords,
           'profile': 'driving-hgv',
           'metrics': ['distance'],
           'units':'m'
           }

# jika destination, source tidak dispesifikasikan dalam request, maka source akan mengembalikan nilai entry hanya satu [0] dan destination hilang
# kemudian jarak akan dihitung dari lokasi 0 ke semua lokasi di daftar lokasi

headers = {
        'Accept': 'application/json, application/geo+json, application/gpx+xml, img/png; charset=utf-8',
        'Authorization': '',
        'Content-Type': 'application/json; charset=utf-8'
    }

url = f'https://ds-route-service-api.pupuk.in/ors/v2/matrix/driving-hgv'
try:
    # Mengirim permintaan POST
    response = requests.post(url=url, headers=headers, json=request)
    response.raise_for_status()  # Raise error jika status code bukan 2xx

    # Parsing hasil
    village_matrix = response.json()
    distances = village_matrix.get('distances', [])
    
    print("Calculated {}x{} routes.".format(len(distances), len(distances[0])))

except requests.exceptions.RequestException as e:
    response = response.json()
    print("An error occurred while making the request:")
    print(f"Code: {response['error']['code']}\nMessage: {response['error']['message']}")

except KeyError as e:
    print("Response format error. Missing key:", e)

except Exception as e:
    print("An unexpected error occurred:", e)

Calculated 63x63 routes.


## **Split Demand Function**
Blok ini berusaha untuk melakukan split data kolom **demands** menyesuaikan dengan variable input **vehicle_capacity**. 

Contoh: jika titik A memiliki demand 17, dengan vehicle capacity adalah 8, maka pemecahan data akan dilakukan menjadi [8, 8, 1] untuk demand, sedangkan kolom data lain akan di salin menyesuaikan jumlah banyak data yang dipecah. Fungsi dibawah **MENGASUMSIKAN** kapasitas vehicle untuk setiap kendaraan adalah **SAMA**.

Diperlukan karena pengoptimasian menggunakan OR-TOOLS hanya bisa dilakukan jika **demand berada dibawah atau sama dengan kapasitas kendaraan** itu sendiri. Jika tidak, maka pengoptimalan rute tidak bisa dilakukan.

Data diubah ke bentuk **array list** dengan tujuan supaya distance matrix yang memiliki struktur nxn yang telah dihasilkan dapat dimasukkan ke dalam urutan baris.

Return tambahan yang dihasilkan fungsi ini adalah
1. distance matrix
2. vehicle capacities
3. number of vehicle
4. depot -> indeks ke 0 dari data
5. mapping -> Array yang berusaha mengidentifikasi customer asli yang telah mengalami pemecahan (splitting) dengan menambahkan angka dibelakang koma dengan struktur seperti ini (indeks konsumen asli, bagian ke-n + 1). Misal, konsumen dengan indeks ke 8 berhasil di split oleh function menjadi 3 bagian, sehingga yang muncul adalah (8,1), (8,2), (8,3)

In [7]:
def split_demands(data):
    max_capacity = data["vehicle_capacities"][0]  # Asumsi semua kendaraan memiliki kapasitas yang sama
    new_name = []
    new_address = []
    new_province = []

    new_demands = []
    new_distance_matrix = []
    new_locations = []
    mapping = []  # Untuk melacak indeks baru ke indeks asli dan sub bagian
    
    for i, demand in enumerate(data["demands"]):
        if demand > max_capacity:
            # Hitung jumlah split yang diperlukan
            num_splits = -(-demand // max_capacity)
            num_splits = int(num_splits)
            split_values = [max_capacity] * (num_splits - 1) + [demand % max_capacity or max_capacity]
            
            # Tambahkan demand hasil split
            for part, split_value in enumerate(split_values):
                new_demands.append(split_value)
                mapping.append((i, part + 1))  # (konsumen asli, bagian ke-n)
            
            # Duplikasi baris dan kolom di distance_matrix untuk konsumen ini
            for _ in split_values:
                new_distance_matrix.append(data["distance_matrix"][i])
            
            for _ in split_values:
                new_locations.append(data['locations'][i])

            for _ in split_values:
                new_name.append(data['name'][i])

        else:
            new_demands.append(demand)
            mapping.append((i, 0))  # (konsumen asli, tidak di-split)

            new_name.append(data['name'][i])
            new_address.append(data['address'][i])
            new_province.append(data['province'][i])
            
            new_distance_matrix.append(data["distance_matrix"][i])
            new_locations.append(data['locations'][i])
    
    # Perbarui distance_matrix dengan menambahkan kolom baru
    updated_matrix = []
    for i, row in enumerate(new_distance_matrix):
        updated_row = []
        for j, _ in enumerate(new_distance_matrix):
            if i < len(mapping) and j < len(mapping):
                updated_row.append(data["distance_matrix"][mapping[i][0]][mapping[j][0]])  # Ambil jarak dari indeks asli
            else:
                updated_row.append(0)  # Atur jarak untuk posisi baru yang di-split
        updated_matrix.append(updated_row)
    
    return {
        "name": new_name,
        "address": new_address,
        "province": new_province,
        "distance_matrix": updated_matrix,
        "demands": new_demands,
        'locations': new_locations,
        "vehicle_capacities": data["vehicle_capacities"],
        "num_vehicles": data["num_vehicles"],
        "depot": data["depot"],
        "mapping": mapping,
    }


## **Data Insert Function**
Blok ini bertujuan untuk mengonversi data dari objek **dataset** ke dalam bentuk **dictionary (key, value)** agar lebih fleksibel dalam mengelola data, khususnya untuk key **distance matrix** yang memiliki banyak array list. Selain itu, format ini memudahkan proses penyimpanan hasil dalam bentuk file JSON, sehingga data dapat dengan mudah dikirimkan ke berbagai platform.

Hal yang harus diperhatikan
1. Data **distance_matrix** dan **demands** harus berbentuk **bilangan bulat (int)**, sehingga dalam fungsi dibawah dibulatkan ke atas
2. Jumlah array dalam **vehicle_capacities** berjumlah sama dengan jumlah kendaraan. Karena pada dasarnya bagian ini memperlihatkan masing-masing kapasitas untuk jumlah kendaraan tersebut. Kapasitas dapat diubah sesuai kebutuhan untuk masing-masing kendaraan, tetapi dalam kasus ini diasumsikan setiap kendaraan memiliki **kapasitas yang sama**
3. **depot** = 0 berarti indeks baris ke-0 dianggap sebagai depot tersebut.

Data yang telah dimasukkan ke dalam dictionary data akan mengembalikan nilai data yang telah di-*split* menggunakan **split_demands function**

In [8]:
# data insert
# (When there's only one vehicle, it reduces to the Traveling Salesperson Problem.)
# A better way to define optimal routes is to minimize the length of the longest single route among all vehicles. This is the right definition if the goal is to complete all deliveries as soon as possible.
# djikstra, mencari minimum weight dari satu titik ke titik lain. TSP = djikstra + rute kembali. VRP = TSP dengan vehicle > 1

def create_data_model():
    data = {}
    """Stores the data for the problem."""
    data['name'] = dataset['Name']
    data['address'] = dataset['Address']
    data['province'] = dataset['Provinsi']
    data["locations"] = list(zip(dataset['Latitude'], dataset['Longitude']))
    data['distance_matrix'] = [[math.ceil(value) if value is not None else 0 for value in row] for row in distances] # dibulatkan keatas
    data["demands"] = list(math.ceil(value) for value in dataset['Demand']) # dibulatkan keatas
    data["vehicle_capacities"] = [vehicle_capacity for _ in range(num_vehicle)]
    data["num_vehicles"] = num_vehicle
    data["depot"] = 0
    
    return split_demands(data)

## **OR-TOOLS Function**
Blok ini berusaha mengembalikan hasil kalkulasi perhitungan urutan titik optimal pengantaran ke konsumen oleh OR-TOOLS Library dengan memanfaatkan **urutan indeks** untuk identifikasi baris data/array.

#### **Main Function**
Fungsi untuk menjalankan fungsi lainnya dan tempat semua data, manager, routing dan solution di *define*. Terdapat empat input utama yang perlu di-*define*.

| Komponen  | Deskripsi                                                                                                                                                                                                                                             |
|-----------|---------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| **`Data`**  | Data dari fungsi `create_data_model` yang telah dibuat sebelumnya.                                                                                                                                                                                    |
| **`Manager`** | Kelas dalam library yang berfungsi untuk menerjemahkan indeks asli ke indeks solver atau sebaliknya, serta mengatur informasi masalah. Menggunakan fungsi **`RoutingIndexManager`** dengan tiga input utama: jumlah lokasi, jumlah kendaraan, dan indeks depot. Manager digunakan untuk menerjemahkan indeks asli ke indeks solver untuk memperoleh **jarak** dan **demand** antar titik menggunakan **`distance_callback`** dan **`demand_callback`**, mendefinisikan dan mendaftarkan panggilan balik (callback) ke solver sebagai **`transit_callback_index`**, menggunakan objek ini di **`SetArcCostEvaluatorOfAllVehicles`** untuk menghitung biaya perjalanan guna menentukan **urutan titik kunjungan optimal** yang mempertimbangkan jarak, serta menambahkan variabel lain (selain jarak) dengan memanggil kembali fungsi **`SetArcCostEvaluatorOfAllVehicles`**. |
| **`Routing`** | Fungsi yang memanfaatkan manager yang telah didefinisikan untuk mengelola model optimasi. Bertugas untuk mengatur perhitungan biaya perjalanan dengan **`routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)`**, mengatur permintaan **demands** dengan **`routing.RegisterUnaryTransitCallback(demand_callback)`**, menambahkan constraint berupa kapasitas kendaraan dengan **`routing.AddDimensionWithVehicleCapacity`**, dan mendaftarkan callback jarak menggunakan **`routing.RegisterTransitCallback(distance_callback)`**. |
| **`Solution`** | Mengembalikan hasil perhitungan solver menggunakan beberapa parameter yang telah ditentukan sebelumnya.                                                                                                                                             |

Source: https://developers.google.com/optimization/routing/cvrp

-> **`AddDimensionWithVehicleCapacity`**, model yang mempertimbangkan kapasitas kendaraan sebagai pertimbangan memperoleh rute. Ada beberapa input yang dapat disesuaikan disini
| Komponen                 | Deskripsi                                                                                                                                                                                      |
|------------|------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| **`callback_index`**        | Indeks untuk panggilan balik yang mengembalikan kuantitas. Indeks ini, yang merupakan referensi internal solver ke *callback*, dibuat oleh metode seperti **RegisterTransitCallback** atau **RegisterUnitaryTransitCallback**. |
| **`slack_max`**             | Menentukan **waktu tunggu tambahan (waktu ngaret)** saat mengunjungi nodes tertentu. Contohnya, jika perjalanan waktu kumulatif ke nodes A adalah 100 menit dan hal yang sama ke nodes B juga 100 menit, dengan waktu perjalanan dari A ke B adalah 75 menit, maka waktu tunggu adalah 25 menit per node. Atur ini ke 0 jika tidak ada waktu tunggu (seperti dalam model ini). |
| **`capacity`**              | Kapasitas per masing-masing kendaraan.                                                                                                                                                            |
| **`fix_start_cumulative_to_zero`** (boolean) | Jika true, nilai kuantitas kumulatif dimulai dari 0.                                                                                                                                          |
| **`dimension_name`**        | String untuk menamai dimensi yang dapat digunakan untuk mengakses variabel dalam program.                                                                                                        |

Source: https://developers.google.com/optimization/routing/dimensions

-> **`search parameter`**, parameter yang digunakan untuk melakukan pencarian urutan titik kunjungan optimal. Ada dua jenis untuk menghasilkan solusi, pertama menggunakan **first solution strategy**, kedua menggunakan pencarian yang lebih *advanced* menggunakan **Local Searh Metaheuristic**. Pada kode kali ini menggunakan pencarian *advanced* menggunakan **Guided Local Search** untuk mencegah *solver* terjebak pada local minimum yang mungkin tidak pada titik optimalnya jika dibandingkan dengan global minimum.

Source: https://developers.google.com/optimization/routing/routing_options


#### **Print Solution**
Fungsi ini berusaha untuk mengembalikan nilai berupa teks hasil optimasi urutan titik kunjungan. Menggunakan pengulangan *For*, menempatkan masing-masing kendaraan yang berbeda berdasarkan indeks secara acak untuk memenuhi sejumlah demand yang diperlukan dengan mempertimbangkan jarak antar titik. Fungsi ini juga dapat memperoleh estimasi **`jumlah jarak (total_distance)`**, **`jumlah muatan (total_load)`**, dan **`total perjalanan (total_trips)`**. Fungsi ini juga dapat melakukan *tracking* seperti jumlah kapasitas sisa dalam kendaraan (remaining_load), jumlah *demand* yang telah berhasil dipenuhi, estimasi jarak, indeks kendaraan ke berapa, hingga nama konsumen.

#### **Get Routes**
Mereplikasi kode dari print_solution yang digunakan khusus untuk hanya mengambil nilai-nilai yang dihasilkan oleh Solver yang kemudian akan diteruskan ke endpoint `direction` untuk menciptakan rutenya di map

In [9]:
"""Capacited Vehicles Routing Problem (CVRP) using OR-TOOLS."""

result_data = []
def print_solution(data, manager, routing, solution):
    """Prints solution on console."""
    mapping = data["mapping"]
    print(f"Objective: {solution.ObjectiveValue()}")
    total_distance = 0
    total_load = 0
    total_trips = 0
    vehicle_id = 0

    for vehicle_id in range(data["num_vehicles"]):
        index = routing.Start(vehicle_id)
        plan_output = f"Route for vehicle {vehicle_id}:\n"
        route_distance = 0
        route_load = 0
        remaining_load_capacity = data["vehicle_capacities"][vehicle_id]  # Track the remaining capacity
        
        while not routing.IsEnd(index):
            node_index = manager.IndexToNode(index)
            consumer_original, split_part = mapping[node_index]  # Ambil indeks asli dan bagian split
            consumer_label = f"{consumer_original}-{split_part}"

            route_load += data["demands"][node_index]
            remaining_load_capacity -= data["demands"][node_index]  # Subtract the demand from remaining capacity

            if node_index == data['depot']:
                plan_output += f"Depot: {data['name'][node_index]} | Cumm_Load: {route_load} | rem_capacity: {remaining_load_capacity} -> "
            elif data['demands'][node_index] == 0:
                index = solution.Value(routing.NextVar(index))
                continue
            else:
                plan_output += f"Consumer: {data['name'][node_index]} | Demand: {data['demands'][node_index]} | Cumm_Load: {route_load} | rem_capacity: {remaining_load_capacity} -> "
            
            previous_index = index
            index = solution.Value(routing.NextVar(index))
            route_distance += routing.GetArcCostForVehicle(
                previous_index, index, vehicle_id
            )

            # Ambil data lokasi pertama dan kedua
            lat_current, lon_current = data['locations'][node_index]  # Koordinat untuk node saat ini
            # lat_next, lon_next = data['locations'][index]  # Koordinat untuk node berikutnya

            # Append data for DataFrame
            # Append current and next node to result_data
            if route_load != 0:
                result_data.append({
                    "Vehicle": vehicle_id,
                    "Depot": data['depot'],
                    "Node": consumer_label,
                    "Demand": data["demands"][node_index],
                    "Cumulative Load": route_load,
                    "Remaining Load Capacity": remaining_load_capacity,
                    "Distance": route_distance,
                    "Current Node": node_index,
                    "Current_lat": lat_current,
                    "Current_lon": lon_current,
                    "Next Node": index,
                })
        # After visiting all customers, return to depot (node 0)
        node_index = manager.IndexToNode(previous_index)
        consumer_original, split_part = mapping[node_index]
        # route_distance += routing.GetArcCostForVehicle(previous_index, index, vehicle_id)

        if route_load != 0:
            plan_output += f"\nLast Customer: {data['name'][node_index]} Load({route_load})\n"
            plan_output += f"Distance of the route: {route_distance}m\n"
            plan_output += f"Load of the route: {route_load}\n"
            total_trips += 1
            total_distance += route_distance
            total_load += route_load
            print(plan_output)

    print(f"Total number of trips: {total_trips}")
    print(f"Total distance of all routes: {total_distance}m")
    print(f"Total load of all routes: {total_load}")

routes = {}
def get_routes(solution, routing, manager, data):
    """Get vehicle routes from a solution and store them in a dictionary."""
    # Get vehicle routes and store them in a dictionary:
    # routes[vehicle_id] = [{'name': <name>, 'location': <location>}, ...]
    for vehicle_id in range(routing.vehicles()):
        index = routing.Start(vehicle_id)
        route = []  # List untuk menyimpan dictionary {'name': ..., 'location': ...}

        while not routing.IsEnd(index):
            node_index = manager.IndexToNode(index)
            if data['demands'][node_index] != 0 or node_index == data['depot']:
                route.append({
                    'name': data['name'][node_index],
                    'location': data['locations'][node_index]
                })
            index = solution.Value(routing.NextVar(index))

        # Tambahkan node terakhir (end/depot)
        node_index = manager.IndexToNode(index)
        route.append({
            'name': data['name'][node_index],
            'location': data['locations'][node_index]
        })

        # Simpan ke dalam dictionary hanya jika rute memiliki lebih dari dua lokasi (depot + customer)
        if len(route) != 2:
            routes[vehicle_id] = route
    
    return routes

def main():
    """Solve the CVRP problem."""
    # Instantiate the data problem.
    data = create_data_model()

    # Create the routing index manager.
    manager = pywrapcp.RoutingIndexManager(
        len(data["distance_matrix"]), data["num_vehicles"], data["depot"]
    )

    # Create Routing Model.
    routing = pywrapcp.RoutingModel(manager)

    # Create and register a transit callback (menghitung jarak antar dua titik).
    def distance_callback(from_index, to_index):
        """Returns the distance between the two nodes."""
        # Convert from routing variable Index to distance matrix NodeIndex.
        from_node = manager.IndexToNode(from_index)
        to_node = manager.IndexToNode(to_index)
        return data["distance_matrix"][from_node][to_node]

    transit_callback_index = routing.RegisterTransitCallback(distance_callback)

    # Define cost of each arc.
    routing.SetArcCostEvaluatorOfAllVehicles(transit_callback_index)

    # Add Capacity constraint.
    def demand_callback(from_index):
        """Returns the demand of the node."""
        # Convert from routing variable Index to demands NodeIndex.
        from_node = manager.IndexToNode(from_index)
        return data["demands"][from_node]

    demand_callback_index = routing.RegisterUnaryTransitCallback(demand_callback)
    routing.AddDimensionWithVehicleCapacity(
        demand_callback_index,
        0,  # null capacity slack
        data["vehicle_capacities"],  # vehicle maximum capacities
        True,  # start cumul to zero
        "Capacity",
    )

    # Setting first solution heuristic.
    search_parameters = pywrapcp.DefaultRoutingSearchParameters()

    search_parameters.local_search_metaheuristic = (
        routing_enums_pb2.LocalSearchMetaheuristic.GUIDED_LOCAL_SEARCH
    )
    search_parameters.time_limit.FromSeconds(10)
    # search_parameters.log_search = True

    # Solve the problem.
    solution = routing.SolveWithParameters(search_parameters)

    # Print solution on console.
    if solution:
        print_solution(data, manager, routing, solution)
        print("\n------------------------- Route Index ----------------------------")

        routes = get_routes(solution, routing, manager, data)
        for vehicle_id, route in routes.items():
            print(f"Route for vehicle {vehicle_id}:")
            
            locations = [stop['name'] for stop in route]
            # Membuat list koordinat lokasi
            coordinates = [str(stop['location']) for stop in route]
            
            # Gabungkan keduanya dan print dalam satu baris
            print(f" - Locations: {', '.join(locations)}")
            print(f" - Coordinates: {', '.join(coordinates)}")
    else:
        print('No Solution Found!')
    

if __name__ == "__main__":
    main()

Objective: 7309901
Route for vehicle 1718:
Depot: DC24 | Cumm_Load: 0 | rem_capacity: 8 -> Consumer: BRATI | Demand: 8 | Cumm_Load: 8 | rem_capacity: 0 -> 
Last Customer: BRATI Load(8)
Distance of the route: 68446m
Load of the route: 8

Route for vehicle 1719:
Depot: DC24 | Cumm_Load: 0 | rem_capacity: 8 -> Consumer: BRATI | Demand: 8 | Cumm_Load: 8 | rem_capacity: 0 -> 
Last Customer: BRATI Load(8)
Distance of the route: 68446m
Load of the route: 8

Route for vehicle 1720:
Depot: DC24 | Cumm_Load: 0 | rem_capacity: 8 -> Consumer: KARANGAWEN | Demand: 8 | Cumm_Load: 8 | rem_capacity: 0 -> 
Last Customer: KARANGAWEN Load(8)
Distance of the route: 65114m
Load of the route: 8

Route for vehicle 1721:
Depot: DC24 | Cumm_Load: 0 | rem_capacity: 8 -> Consumer: KARANGAWEN | Demand: 8 | Cumm_Load: 8 | rem_capacity: 0 -> 
Last Customer: KARANGAWEN Load(8)
Distance of the route: 65114m
Load of the route: 8

Route for vehicle 1722:
Depot: DC24 | Cumm_Load: 0 | rem_capacity: 8 -> Consumer: SUMBERS

## **Decode Geometry Function**
Blok ini berusaha untuk memecah enkripsi geometry yang dihasilkan oleh **API ORS Endpoint Direction** ke dalam bentuk koordinat lokasi titik rute jalan untuk mencapai lokasi. Output berupa geojson dengan tipe `LineString`. Kode ini bisa didapatkan dalam dokumentasi Open Route Service di *link* berikut

Source: https://giscience.github.io/openrouteservice/api-reference/endpoints/directions/geometry-decoding#geometry-decoding

In [59]:
def decode_polyline(polyline, is3d=False):
    """Decodes a Polyline string into a GeoJSON geometry.
    :param polyline: An encoded polyline, only the geometry.
    :type polyline: string
    :param is3d: Specifies if geometry contains Z component.
    :type is3d: boolean
    :returns: GeoJSON Linestring geometry
    :rtype: dict
    """
    points = []
    index = lat = lng = z = 0

    while index < len(polyline):
        result = 1
        shift = 0
        while True:
            b = ord(polyline[index]) - 63 - 1
            index += 1
            result += b << shift
            shift += 5
            if b < 0x1F:
                break
        lat += (~result >> 1) if (result & 1) != 0 else (result >> 1)

        result = 1
        shift = 0
        while True:
            b = ord(polyline[index]) - 63 - 1
            index += 1
            result += b << shift
            shift += 5
            if b < 0x1F:
                break
        lng += ~(result >> 1) if (result & 1) != 0 else (result >> 1)

        if is3d:
            result = 1
            shift = 0
            while True:
                b = ord(polyline[index]) - 63 - 1
                index += 1
                result += b << shift
                shift += 5
                if b < 0x1F:
                    break
            if (result & 1) != 0:
                z += ~(result >> 1)
            else:
                z += result >> 1

            points.append(
                [
                    round(lng * 1e-5, 6),
                    round(lat * 1e-5, 6),
                    round(z * 1e-2, 1),
                ]
            )

        else:
            points.append([round(lng * 1e-5, 6), round(lat * 1e-5, 6)])

    geojson = {u"type": u"LineString", u"coordinates": points}

    return geojson

## **Open Route Service "Direction" Endpoint**
Blok ini berusaha untuk memperoleh respons berupa titik koordinat sebagai penunjuk untuk memperoleh rute sebenarnya melalui koordinat titik lokasi yang kita miliki. Rute yang digambarkan tergantung dari preference yang diberikan dalam body JSON. Contoh: jika kita memilih "shortest" preference dan input lokasi ada 3 koordinat, maka ia akan menggambarkan rute "terpendek" pada masing-masing koordinat itu. Untuk masing-masing key pada body bisa dilihat pada spreadsheet ini yang sudah dirangkumkan

**`Key Parameter Direction ORS`**
https://docs.google.com/spreadsheets/d/1ULUxCrFwf_ATbDZsC4M7C6muDTdUlJSCxojhaTb5PIE/edit?usp=sharing

Untuk dokumentasi lengkap dan menyeluruh dapat dilihat pada tautan berikut
https://giscience.github.io/openrouteservice/

*Kode di bawah ini mengambil seluruh koordinat lokasi, kemudian menambahkan koordinat depot di akhir sebagai titik penutup rute untuk memvisualisasikan putaran rute acak yang dihasilkan oleh ORS.

In [60]:
village_coords.append(village_coords[0])
url_direction = "https://ds-route-service-api.pupuk.in/ors/v2/directions/driving-hgv"

units = 'km'

request = {"coordinates": village_coords,
           "geometry": "true",
           "radiuses":-1,
           "preference": "shortest",
           "units":units
           }
random_route = requests.post(url=url_direction,headers=headers,json=request)
random_route = random_route.json()
random_route = [random_route]
random_route

[{'bbox': [110.685905, -7.535937, 110.90175, -7.239456],
  'routes': [{'summary': {'distance': 1738.891,
     'duration': 239795.10000000003},
    'segments': [{'distance': 8.123,
      'duration': 636.2,
      'steps': [{'distance': 0.09,
        'duration': 21.5,
        'type': 11,
        'instruction': 'Head west',
        'name': '-',
        'way_points': [0, 1]},
       {'distance': 0.47,
        'duration': 94.4,
        'type': 0,
        'instruction': 'Turn left',
        'name': '-',
        'way_points': [1, 7]},
       {'distance': 7.188,
        'duration': 457.3,
        'type': 3,
        'instruction': 'Turn sharp right onto Jalan Gemolong-Karanggede, 258',
        'name': 'Jalan Gemolong-Karanggede, 258',
        'way_points': [7, 119]},
       {'distance': 0.094,
        'duration': 11.3,
        'type': 2,
        'instruction': 'Turn sharp left',
        'name': '-',
        'way_points': [119, 121]},
       {'distance': 0.133,
        'duration': 16.0,
        '

Blok ini berusaha memperoleh hasil response berupa koordinat jalan yang ditempuh oleh masing-masing kendaraan yang telah dioptimasi berdasarkan urutan kunjungan optimal per indeks kendaraan ke titik konsumen hingga kembali lagi ke depot yang dimasukkan ke dalam list *`result_route_optimal`*.

In [65]:
# Daftar vehicle_id yang ingin diproses
coordinates_dict = {}

for vehicle_id, stops in routes.items():
    coordinates_list = [(stop['location'][1], stop['location'][0]) for stop in stops]  # Membalikkan lat lon menjadi lon lat
    coordinates_dict[str(vehicle_id)] = coordinates_list  # Menyimpan koordinat dengan vehicle_id sebagai key

vehicle_id_list = [vehicle_id for vehicle_id, coords in coordinates_dict.items()]

# List untuk menyimpan hasil response untuk setiap vehicle_id
result_route_optimal = []

# Mengirimkan request untuk setiap vehicle_id
for vehicle_id in vehicle_id_list:
    # Mengambil koordinat berdasarkan vehicle_id dari coordinates_dict
    if vehicle_id in coordinates_dict:
        coordinates = coordinates_dict[vehicle_id]
        request['coordinates'] = coordinates
        
        # Mengirimkan POST request untuk mendapatkan optimal route
        optimal_route_response = requests.post(url=url_direction, headers=headers, json=request)

        # Mengonversi response ke format JSON
        if optimal_route_response.status_code == 200:
            optimal_route = optimal_route_response.json()
            print(f"Optimal route for {vehicle_id}: {optimal_route}")
            # Menambahkan hasil response ke dalam list result_route_optimal
            result_route_optimal.append({
                f'{vehicle_id}': optimal_route
            })
        else:
            response = optimal_route_response.json()
            print(f"Error with vehicle {vehicle_id}: {response}")
            # Menambahkan error response ke dalam list
            result_route_optimal.append({
                'vehicle_id': vehicle_id,
                'error': f"Error {response}"
            })
    else:
        print(f"Coordinates not found for vehicle {vehicle_id}")
        # Menambahkan error response ke dalam list jika koordinat tidak ditemukan
        result_route_optimal.append({
            'vehicle_id': vehicle_id,
            'error': 'Coordinates not found'
        })

# Menampilkan semua hasil yang tersimpan di result_route_optimal
print("Result Route Optimal:")
print(result_route_optimal)

Optimal route for 1472: {'bbox': [110.799667, -7.52369, 110.90175, -7.388474], 'routes': [{'summary': {'distance': 49.93, 'duration': 5902.1}, 'segments': [{'distance': 31.843, 'duration': 4248.0, 'steps': [{'distance': 0.105, 'duration': 25.2, 'type': 11, 'instruction': 'Head east', 'name': '-', 'way_points': [0, 2]}, {'distance': 0.532, 'duration': 127.6, 'type': 1, 'instruction': 'Turn right', 'name': '-', 'way_points': [2, 11]}, {'distance': 0.578, 'duration': 34.7, 'type': 0, 'instruction': 'Turn left onto Jalan Gemolong-Karanggede, 258', 'name': 'Jalan Gemolong-Karanggede, 258', 'way_points': [11, 23]}, {'distance': 0.265, 'duration': 63.6, 'type': 1, 'instruction': 'Turn right', 'name': '-', 'way_points': [23, 26]}, {'distance': 0.164, 'duration': 39.4, 'type': 0, 'instruction': 'Turn left', 'name': '-', 'way_points': [26, 29]}, {'distance': 0.882, 'duration': 105.8, 'type': 1, 'instruction': 'Turn right', 'name': '-', 'way_points': [29, 42]}, {'distance': 0.249, 'duration': 29.

JSONDecodeError: Expecting value: line 1 column 1 (char 0)

Fungsi untuk membedakan koordinat yang merupakan depot dan konsumen yang kemudian akan dibedakan dari warna dan iconnya

In [66]:
distance_list = []
duration_list = []
for i, value in enumerate(result_route_optimal):
    for vehicle_id in vehicle_id_list:

        if vehicle_id in value:
            routes = value[vehicle_id]['routes']
            coords = value[vehicle_id]['metadata']['query']['coordinates']
            
            for k, route in enumerate(routes):
                geometry = route['geometry']
                distance = route['summary']['distance']
                duration = route['summary']['duration']
                distance_list.append(distance)
                duration_list.append(duration)

sum_angka = sum(distance_list)
sum_duration = sum(duration_list) / 60
print(f"Sum of Distance Recommended: {sum_angka:.0f} {units}")
print(f"Sum of Distance Recommended: {math.ceil(sum_duration):.0f} hours")
print(f"Number of Amount Trips in: {len(vehicle_id_list)}")

Sum of Distance Recommended: 10254 km
Sum of Distance Recommended: 24539 hours
Number of Amount Trips in: 528


In [14]:
depot_loc = dataset[['Longitude','Latitude']].head(1).values.tolist()
consumer_loc = dataset[['Longitude', 'Latitude']].iloc[1:].values.tolist()

depot_coord = [depot_loc[0][0], depot_loc[0][1]]
def color_depot(coords, default_color):
    if coords == depot_coord:
        return "red"
    else:
        return default_color

def icon_depot(coords, default_icon):
    if coords == depot_coord:
        return "home"
    else:
        return default_icon

def layer_control(coords, name, control=True, show=True):
    if coords == depot_coord:
        fg = folium.FeatureGroup(name, control==False, show)
    else:
        fg = folium.FeatureGroup(name, control==control, show)
    return fg


## **Plotting to Map**
Blok ini berusaha untuk menggambarkan koordinat yang dihasilkan oleh API "Direction" ke dalam folium map, baik dari penggambaran titik lokasi (Marker), penggambaran rute menggunakan polyline yang koordinat rute diperoleh melalui fungsi decode_polyline. Kemudian, setiap indeks vehicle akan diwarnai dengan warna yang berbeda untuk membedakan dengan vehicle lain. Kemudian ditambahkan keterangan waktu dan jarak yang ditempuh.

Peta bisa disimpan dalam bentuk html dengan menggunakan method `save` yang ada pada library folium.

In [67]:
m = folium.Map(location=(dataset['Latitude'].mean(), dataset['Longitude'].mean()), zoom_start=8)
fg_icon = folium.FeatureGroup(name='Icon Collection', show=True).add_to(m)
fg_line = folium.FeatureGroup(name='Route', show=False).add_to(m)
fg_line_opt = folium.FeatureGroup(name='Route Optimization', show=False).add_to(m)
marker_cluster_icon = MarkerCluster().add_to(fg_icon)
marker_cluster_line = MarkerCluster().add_to(fg_line)
marker_cluster_opt = MarkerCluster().add_to(fg_line_opt)
folium.map.LayerControl().add_to(m)

# marker icon
for _,row in dataset.iterrows():
    name = row['Name']
    lat = row['Latitude']
    lon = row['Longitude']
    coords = [lat,lon]

    reversed_coords = list(reversed(coords))
    popup = "<strong>{0}</strong><br>Lat: {1:.3f}<br>Long: {2:.3f}".format(name, lat, lon)
    icon = folium.Icon(
        color=color_depot(reversed_coords,"blue"),
        icon_color='white',
        icon=icon_depot(reversed_coords,"info"),  # fetches font-awesome.io symbols
        prefix='fa')
    marker = folium.Marker(coords, icon=icon, popup=popup)
    marker.add_to(fg_icon)

# get random route using direction API Open Route Service
line_colors = ['green', 'orange', 'blue', 'yellow']

decode_geometries = []
# Loop untuk mendekode setiap geometry dari alternatif rute (enumerate untuk bentuk list)
for i, responses in enumerate(random_route):
    color = line_colors[i % len(line_colors)]
    routes = responses['routes']
    coords = responses['metadata']['query']['coordinates']
    # preference = responses['preference']

    for j, route in enumerate(routes):
        geometry = route['geometry']
        distance = route['summary']['distance']
        duration = route['summary']['duration']
        decoded = decode_polyline(geometry)['coordinates']  # Decode geometry
        decode_geometries.append(decoded)  # Simpan ke daftar
        for i, coord in enumerate(coords):
            line = folium.PolyLine(
                locations=[list(reversed(coord)) for coord in decoded],
                color=color,
                weight=5,
                opacity=0.5,
                popup=f"Distance:{distance}{units} \n Duration:{duration / 60:.2f}min"
            )
            marker_cluster_line.add_child(line)

# Memuat file JSON dan mengonversinya menjadi list
color_codes_json_path = 'color_codes.json'

with open(color_codes_json_path, 'r') as file:
    color_codes = json.load(file)

line_colors_opt = color_codes
# get optimize route using direction API Open Route Service based on sequence coordinate OR-TOOLS
decode_dict = {}
for i, value in enumerate(result_route_optimal):
    for vehicle_id in vehicle_id_list:
        color = line_colors_opt[i % len(line_colors_opt)]
        if vehicle_id not in decode_dict:
            decode_dict[vehicle_id] = {}
        # Periksa jika vehicle_id ada di value
        if vehicle_id in value:
            # print(f'{vehicle_id}, {value}')
            routes = value[vehicle_id]['routes']
            coords = value[vehicle_id]['metadata']['query']['coordinates']
            
            for k, route in enumerate(routes):
                geometry = route['geometry']
                distance = route['summary']['distance']
                duration = route['summary']['duration']
                decoded = decode_polyline(geometry)['coordinates']
                decode_dict[vehicle_id] = decoded

                with open('decoded.json', 'w') as file:
                    json.dump(decode_dict, file)

                for i, coord in enumerate(coords):
                    line_opt = folium.PolyLine(
                        locations=[list(reversed(coord)) for coord in decoded],
                        color=color,
                        weight=2,
                        opacity=0.7,
                        popup=f"Distance:{distance}{units} \n Duration:{duration / 60:.2f}min",
                    )
                    marker_cluster_opt.add_child(line_opt)

m.save(map_name)